In [1]:
#import model
import numpy as np
import pandas as pd
from agents_vec import gulden_vectorised
# from functions import regularise

#import tuning library
# !pip install ray
!pip install -U "ray[default]"
!pip install bayesian-optimization
!pip install optuna
import bayes_opt
import optuna

import ray
from ray import air, tune, train
from ray.air import session
from hyperopt import hp
from ray.tune.search.hyperopt import HyperOptSearch
from scipy.stats import spearmanr, kendalltau
from scipy.stats import linregress

from ray.tune.search.bayesopt import BayesOptSearch

from ray.tune.search.optuna import OptunaSearch
from ray import air

def regularise(df):
    df2 = df
    n=len(df.index.get_level_values(0).unique())
    m=len(df.index.get_level_values(1).unique())
    denominator=np.ones(m*n)
    for i in range(n):
        for j in range(m):
            ind = m*i + j
            denominator[ind] = df.iloc[ind,i]
            df2.iloc[ind,:] = df.iloc[ind,:]/df.iloc[ind,i]

    return df2

def calculate_rca(df):
    # Set the multi-index
    # df = df.set_index(['Group', 'Sector'])

    # Calculate the total output for each sector across all regions
    sector_totals = df.sum(level=1).sum(axis=1)

    # Calculate the total output for each region
    region_totals = df.sum(level=0).sum(axis=1)

    # Calculate global total
    global_total = df.sum().sum()

    # Initialize a DataFrame to store RCA values
    rca_df = pd.DataFrame(index=df.index, columns=df.columns)

    # Calculate RCA for each sector in each region
    for group, sector in df.index:
        sector_value = df.loc[(group, sector)]
        sector_share = sector_value / sector_totals[sector]
        region_share = region_totals[group] / global_total
        rca_value = sector_share / region_share
        rca_df.loc[(group, sector)] = rca_value

    return rca_df

def binarize_rca(df, percentile_threshold=40):
    """
    Binarize the RCA DataFrame.
    Values above the specified percentile threshold will be set to 1, others will be set to 0.

    :param df: DataFrame with RCA values.
    :param percentile_threshold: The percentile to use as a threshold.
    :return: Binarized DataFrame.
    """
    # Flatten the DataFrame to find the global percentile value
    flattened = df.values.flatten()

    # Find the value at the specified percentile
    threshold_value = np.percentile(flattened, percentile_threshold)

    # Binarize the DataFrame based on the threshold
    binarized_df = df.applymap(lambda x: 1 if x > threshold_value else 0)

    return binarized_df

def jaccard_similarity(df1, df2):
    """
    Calculate the Jaccard similarity coefficient between two binarized dataframes.

    :param df1: First binarized DataFrame.
    :param df2: Second binarized DataFrame.
    :return: Jaccard similarity coefficient.
    """
    # Ensure the dataframes are aligned and of the same shape
    if df1.shape != df2.shape:
        raise ValueError("DataFrames must be of the same shape.")

    # Flatten the dataframes
    flat_df1 = df1.values.flatten()
    flat_df2 = df2.values.flatten()

    # Calculate intersection and union
    intersection = sum((flat_df1 == 1) & (flat_df2 == 1))
    union = sum((flat_df1 == 1) | (flat_df2 == 1))

    # Calculate Jaccard similarity
    jaccard_similarity = intersection / union if union != 0 else 0

    return jaccard_similarity

class Tuner:
    def __init__(self, parameters):
        self.parameters=parameters



    def tune_model(self):
      try:
        parameters=self.parameters
        space = {}
        for i in range(parameters["n_countries"]):
            for j in range(parameters["n_products"]):
                space["alpha-"+str(i)+"-"+str(j)]=tune.uniform(0.01, 0.99)
                space["beta-"+str(i)+"-"+str(j)]=tune.uniform(0.01, 0.99)
                space["A-"+str(i)+"-"+str(j)]=tune.uniform(0.01, 5)

        algo = BayesOptSearch(random_search_steps=150)
        # algo = OptunaSearch()

        self.tuner = tune.Tuner(
            tune.with_resources( tune.with_parameters(run_sim,parameters=parameters), resources={"CPU": 8, "memory":32203886388.0 }),
            tune_config=tune.TuneConfig(
                metric="fro_norm",
                mode="min",
                search_alg=algo,
                num_samples=100,
                # make checkpoints every 10 iterations and at the end, keep the best 3
                time_budget_s=42800.0
            ),
            run_config=train.RunConfig(log_to_file=True,
                                       stop={"training_iteration": 100},
                                       failure_config=train.FailureConfig(max_failures=5)),
            param_space=space,
        )
        self.results = self.tuner.fit()
        print(self.results)
        return self.results
      except Exception as e:
        print(f"Error during tuning: {e}")
        return None

def run_sim(config,parameters):
    try:
      A_test=np.ones((n_countries, n_products))
      alpha_test = np.ones((n_countries, n_products))
      beta_test = np.ones((n_countries, n_products))
      for i in range(parameters["n_countries"]):
          for j in range(parameters["n_products"]):
              alpha_test[i][j]=config["alpha-"+str(i)+"-"+str(j)]
              # beta_test[i][j]=1-config["alpha-"+str(i)+"-"+str(j)]
              beta_test[i][j]=config["beta-"+str(i)+"-"+str(j)]
              A_test[i][j]=config["A-"+str(i)+"-"+str(j)]


      production, income, net_exports, df1, df2 =  gulden_vectorised(case="tune_session", n_countries=parameters["n_countries"], n_products=parameters["n_products"], countries=parameters["countries"], products=parameters["products"], citizens_per_nation=parameters["citizens_per_nation"], A=A_test, alpha=alpha_test, beta=beta_test,share=parameters["share"],
                        iterations=parameters["iterations"], Tr_time=parameters["Tr_time"], trade_change=parameters["trade_change"], autarky_time=parameters["autarky_time"], pricing_algorithm=parameters["pricing_algorithm"],
                        utility_algorithm=parameters["utility_algorithm"], wage_algorithm=parameters["wage_algorithm"],

                        csv=False, plot=False, shock=parameters["shock"], shock_time=parameters["shock_time"], cm_time=parameters["cm_time"], d=parameters["d"],
                        innovation=parameters["innovation"], innovation_time=parameters["innovation_time"], gamma=parameters["gamma"], eta=parameters["eta"], weights=parameters["weights"], elasticities=parameters["elasticities"],
                        sigma=parameters["sigma"])


      # # Least squares error
      # df2.head()
      # df2 = df2.set_index(['Group','Sector'])
      df1 = parameters["benchmark"]
      v2=df2.values
      v1=df1.values

      # Basic errors
      abs_error=np.sqrt(np.mean((v1-v2)**2))
      fro_norm=np.linalg.norm(v2-v1, 'fro')
      rel_error=np.linalg.norm(v2-v1, 'fro') / np.linalg.norm(v1, 'fro')
      slope, intercept, r_value, _, _ = linregress(v1.flatten(), v2.flatten())

      # Correlation Metrics
      correlation = np.corrcoef(v1.flatten(), v2.flatten())[0,1]
      spearman_corr, _ = spearmanr(v1.flatten(), v2.flatten())

      # # Thresholded
      # ddf1=df1
      # ddf2=df2
      # # threshold1 = np.percentile(ddf1.values.flatten(), 10)
      # # threshold2 = np.percentile(ddf2.values.flatten(), 10)
      # dv1 = ddf1._get_numeric_data()
      # dv2 = ddf2._get_numeric_data()
      # threshold=0.01
      # dv1[dv1 < threshold] = 0
      # dv2[dv2 < threshold] = 0
      # dv1=dv1.values
      # dv2=dv2.values

      # # Basic errors- thresholded
      # abs_error_t=np.sqrt(np.mean((dv2-dv1)**2))
      # fro_norm_t=np.linalg.norm(dv2-dv1, 'fro')
      # rel_error_t=np.linalg.norm(dv2-dv1, 'fro') / np.linalg.norm(dv1, 'fro')
      # nslope, nintercept, thres_norm_r_value, _, _ = linregress(dv1.flatten(), dv2.flatten())

      #  # Correlation Metrics-thresholded
      # norm_thres_correlation = np.corrcoef(dv1.flatten(), dv2.flatten())[0,1]
      # norm_thres_spearman_corr, _ = spearmanr(dv1.flatten(), dv2.flatten())

      # # Thresholded and binarised
      # df1 = parameters["benchmark"]
      # rca_df1 = calculate_rca(df1)
      # rca_df2 = calculate_rca(df2)
      # binarized_rca_df1 = binarize_rca(rca_df1)
      # binarized_rca_df2 = binarize_rca(rca_df2)
      # rca_error = np.sum((rca_df1.values-rca_df2.values)**2)
      # # rca_correlation = np.corrcoef(rca_df1.values.flatten(), rca_df2.values.flatten())[0,1]
      # jaccard_similarity_value = jaccard_similarity(binarized_rca_df1, binarized_rca_df2)


      # print(error)
      session.report(
          {
              "abs_error":abs_error,
              # "abs_error_t":abs_error_t,
              "fro_norm":fro_norm,
              # "fro_norm_t":fro_norm_t,
              "rel_error":rel_error,
              # "rel_error_t":rel_error_t,
              "r_value":r_value,
              # "r_value_t":thres_norm_r_value,
              "correlation": correlation,
              # "norm_thres_correlation":norm_thres_correlation,
              "spearman": spearman_corr,
              # "norm_thres_spearman_corr":norm_thres_spearman_corr,

          }

      )
      return {
              "abs_error":abs_error,
              # "abs_error_t":abs_error_t,
              "fro_norm":fro_norm,
              # "fro_norm_t":fro_norm_t,
              "rel_error":rel_error,
              # "rel_error_t":rel_error_t,
              "r_value":r_value,
              # "r_value_t":thres_norm_r_value,
              "correlation": correlation,
              # "norm_thres_correlation":norm_thres_correlation,
              "spearman": spearman_corr,
              # "norm_thres_spearman_corr":norm_thres_spearman_corr,
          }

    except Exception as e:

        print(f"Error occurred with parameters {config}: {e}")
        # Optionally, log the error to a file or take other actions

        # Return a default error value or handle it as you see fit
        return {
              "abs_error":abs_error,
              # "abs_error_t":abs_error_t,
              "fro_norm":fro_norm,
              # "fro_norm_t":fro_norm_t,
              "rel_error":rel_error,
              # "rel_error_t":rel_error_t,
              "r_value":r_value,
              # "r_value_t":thres_norm_r_value,
              "correlation": correlation,
              # "norm_thres_correlation":norm_thres_correlation,
              "spearman": spearman_corr,
              # "norm_thres_spearman_corr":norm_thres_spearman_corr,

        }



     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 MB 19.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 201.4/201.4 kB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 71.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.1/98.1 kB 11.1 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.2/128.2 kB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 51.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.4/58.4 kB 6.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.9/468.9 kB 37.3 MB/s eta 0:00:00
  Created wheel for gpustat: filename=gpustat-1.1.1-py3-none-any.whl size=26535 sha256=c8d870869c6ed7d9a7f1823a4f720aef8f6d308316eb49f8c0cd4f97ab578e5a
  Stored in directory: /root/.cache/pip/wheels/ec/d7/80/a71ba354

In [ ]:
n_countries=7
pop = [1000, 388, 208, 157, 808, 510, 271]

n_products=13
# ray.init()
benchmark_matrix = pd.read_csv('IO_cc_primary.csv', index_col=[0,1])
benchmark_matrix = benchmark_matrix.div(benchmark_matrix.sum(axis=1),axis=0)

v=Tuner(parameters={
            "benchmark":benchmark_matrix,
            "n_countries":n_countries,
            "n_products":n_products,
            "countries" : ['{i}'.format(i=i) for i in range(n_countries)],
            "products" : ['{i}'.format(i=i) for i in range(n_products)],
#             "citizens_per_nation" : [100]*n_countries,
            "citizens_per_nation" : pop,

            "iterations":2000,
            "Tr_time":1,
            "trade_change":0.01,
            "autarky_time":15000,
            "pricing_algorithm":'cpmu',
                      "utility_algorithm":'geometric',
            "wage_algorithm":'marginal_product',
                      "share" : np.ones(n_countries),
            "shock":None,
            "shock_time":10000,
            "cm_time":1,
            "d":0.000,
                      "innovation":False,
            "innovation_time":10000,
            "gamma":1,
            "eta":0.01,
            "weights":None,
            "elasticities":None,
                      "sigma":None
        })

#
results = v.tune_model()
if results is not None:
    # Process results
    results=v.tuner.get_results()
    df = results.get_dataframe()
    df.to_csv('/content/drive/MyDrive/ray_results/ray_tune_results_rownorm_frob.csv')

else:
    print("Tuning did not complete successfully.")

2024-02-21 09:02:15,595	INFO worker.py:1715 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2024-02-21 09:02:16,852	INFO tune.py:220 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.
2024-02-21 09:02:16,857	INFO tune.py:592 -- [output] This will use the new output engine with verbosity 1. To disable the new output and use the legacy output engine, set the environment variable RAY_AIR_NEW_OUTPUT=0. For more information, please see https://github.com/ray-project/ray/issues/36949
2024-02-21 09:02:16,881	INFO tensorboardx.py:178 -- pip install "ray[tune]" to see TensorBoard files.
2024-02-21 09:02:16,883	WARNING callback.py:137 -- The TensorboardX logger cannot be instantiated because either TensorboardX or one of it's dependencies is not installed. Please make sure you have the latest version of TensorboardX installed: `pip install -U tensorboardx`


+----------------------------------------------------------------+
| Configuration for experiment     run_sim_2024-02-21_09-02-12   |
+----------------------------------------------------------------+
| Search algorithm                 SearchGenerator               |
| Scheduler                        FIFOScheduler                 |
| Number of trials                 100                           |
+----------------------------------------------------------------+

View detailed results here: /root/ray_results/run_sim_2024-02-21_09-02-12

Trial status: 1 PENDING
Current time: 2024-02-21 09:02:17. Total running time: 0s
Logical resource usage: 0/8 CPUs, 0/0 GPUs
+-----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

  9%|▉         | 185/2000 [00:26<04:14,  7.13it/s]



Trial status: 1 RUNNING | 1 PENDING
Current time: 2024-02-21 09:02:47. Total running time: 30s
Logical resource usage: 8.0/8 CPUs, 0/0 GPUs
+------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

 20%|█▉        | 398/2000 [00:56<03:50,  6.96it/s]


...

 59%|█████▉    | 1189/2000 [02:49<01:54,  7.11it/s]
(run_sim pid=12653) /content/agents_vec.py:217: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   trades_history[:, :, t] = io.values
(run_sim pid=12653) /content/agents_vec.py:219: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   net_exports_history[:, :, t] = net_exports
(run_sim pid=12653) /content/agents_vec.py:227: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   supply[:, :, t] = S
 60%|█████▉    | 1190/2000 [02:49<01:53,  7.14it/s]
(run_sim pid=12653) /content/agents_vec.py:217: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   trades_history[:, :, t] = io.values
(run_sim pid=12653) /content/agents_vec.py:219: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   net_exports_history[:, :, t] = net_exports
(run_sim pid=12653) /content/agents_vec.py:227: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   supply[:, :, t] = S
 60%|███

Trial status: 9 TERMINATED | 1 RUNNING | 1 PENDING
Current time: 2024-02-21 09:48:24. Total running time: 46min 7s
Logical resource usage: 8.0/8 CPUs, 0/0 GPUs
Current best trial: 5aaa4605 with fro_norm=3.4311462138240096 and params={'alpha-0-0': 0.5986380452173887, 'beta-0-0': 0.13054322922127073, 'A-0-0': 3.269282324751102, 'alpha-0-1': 0.7387220378530286, 'beta-0-1': 0.5574695485214168, 'A-0-1': 4.692141044057928, 'alpha-0-2': 0.25930374922501004, 'beta-0-2': 0.8386922757301086, 'A-0-2': 3.3282746683452165, 'alpha-0-3': 0.36461603134103593, 'beta-0-3': 0.6886429701358407, 'A-0-3': 1.308831419254355, 'alpha-0-4': 0.4730434879063833, 'beta-0-4': 0.4313324558423452, 'A-0-4': 4.536903203222091, 'alpha-0-5': 0.054735770592336065, 'beta-0-5': 0.6695072899465437, 'A-0-5': 3.356954236410112, 'alpha-0-6': 0.14722361560225133, 'beta-0-6': 0.2798735507703102, 'A-0-6': 2.8065987485923953, 'alpha-0-7': 0.28127802163547966, 'beta-0-7': 0.31018722880264843, 'A-0-7': 0.5638374513752706, 'alpha-0-8'

 76%|███████▌  | 1519/2000 [03:35<01:08,  7.06it/s]


Trial status: 9 TERMINATED | 1 RUNNING | 1 PENDING
Current time: 2024-02-21 09:48:54. Total running time: 46min 38s
Logical resource usage: 8.0/8 CPUs, 0/0 GPUs
Current best trial: 5aaa4605 with fro_norm=3.4311462138240096 and params={'alpha-0-0': 0.5986380452173887, 'beta-0-0': 0.13054322922127073, 'A-0-0': 3.269282324751102, 'alpha-0-1': 0.7387220378530286, 'beta-0-1': 0.5574695485214168, 'A-0-1': 4.692141044057928, 'alpha-0-2': 0.25930374922501004, 'beta-0-2': 0.8386922757301086, 'A-0-2': 3.3282746683452165, 'alpha-0-3': 0.36461603134103593, 'beta-0-3': 0.6886429701358407, 'A-0-3': 1.308831419254355, 'alpha-0-4': 0.4730434879063833, 'beta-0-4': 0.4313324558423452, 'A-0-4': 4.536903203222091, 'alpha-0-5': 0.054735770592336065, 'beta-0-5': 0.6695072899465437, 'A-0-5': 3.356954236410112, 'alpha-0-6': 0.14722361560225133, 'beta-0-6': 0.2798735507703102, 'A-0-6': 2.8065987485923953, 'alpha-0-7': 0.28127802163547966, 'beta-0-7': 0.31018722880264843, 'A-0-7': 0.5638374513752706, 'alpha-0-8

 76%|███████▋  | 1530/2000 [03:37<01:05,  7.15it/s]
(run_sim pid=12653) /content/agents_vec.py:217: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   trades_history[:, :, t] = io.values
(run_sim pid=12653) /content/agents_vec.py:219: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   net_exports_history[:, :, t] = net_exports
(run_sim pid=12653) /content/agents_vec.py:227: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   supply[:, :, t] = S
 77%|███████▋  | 1531/2000 [03:37<01:06,  7.09it/s]
(run_sim pid=12653) /content/agents_vec.py:217: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   trades_history[:, :, t] = io.values
(run_sim pid=12653) /content/agents_vec.py:219: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   net_exports_history[:, :, t] = net_exports
(run_sim pid=12653) /content/agents_vec.py:227: RuntimeWarning: overflow encountered in cast
(run_sim pid=12653)   supply[:, :, t] = S
 77%|███

In [ ]:
import pandas as pd

ex = pd.read_csv('/content/drive/MyDrive/ray_results/ray_tune_results_reg_ex.csv')
ex = ex.sort_values(by='correlation',ascending=False)

In [ ]:
ex.head()

Unnamed: 0  error_sum  correlation  spearman   rsquare   timestamp  \
364         364   4.639512     0.873308  0.482818  0.762668  1705859105   
270         270   4.651104     0.872691  0.489592  0.761589  1705851429   
73           73   4.650767     0.872625  0.524936  0.761474  1705835457   
35           35   4.652443     0.872592  0.420946  0.761416  1705832391   
366         366   4.653310     0.872561  0.485231  0.761363  1705859268   

     checkpoint_dir_name   done  training_iteration  trial_id  ...  \
364                  NaN  False                   2  066a7baf  ...   
270                  NaN  False                   2  5e27111c  ...   
73                   NaN  False                   2  24d02e7e  ...   
35                   NaN  False                   2  f76310ee  ...   
366                  NaN  False                   2  7c3c2bb8  ...   

    config/alpha-6-10  config/beta-6-10  config/A-6-10  config/alpha-6-11  \
364          0.125762          0.455776      22.735105           0.613243   
270          0.632311          0.220965      30.757797           0.579276   
73           0.637610          0.019549      37.413569           0.695192   
35           0.403058          0.846794      18.734841           0.247594   
366          0.572039          0.853923      45.977033           0.113494   

    config/beta-6-11 config/A-6-11  config/alpha-6-12  config/beta-6-12  \
364         0.719620     27.400396           0.197703          0.998920   
270         0.125870     34.194382           0.019117          0.987518   
73          0.933944     39.256937           0.297479          0.301176   
35          0.681109     35.148780           0.510794          0.269958   
366         0.813740     46.654591           0.009343          0.007257   

     config/A-6-12    logdir  
364      37.025790  066a7baf  
270      30.884587  5e27111c  
73        4.078642  24d02e7e  
35       47.732336  f76310ee  
366      26.667682  7c3c2bb8  

[5 rows x 292 columns]

In [ ]:
import pandas as pd

benchmark_matrix = pd.read_csv('IO_cc_primary.csv', index_col=[0,1])
benchmark_matrix = benchmark_matrix.div(benchmark_matrix.sum(axis=1),axis=0)
benchmark_matrix

East Asia and Pacific  \
Group                 Sector                                                                      
East Asia and Pacific Agriculture                                                      0.982181   
                      Electrical and Machinery                                         0.852470   
                      Fishing                                                          0.981130   
                      Food & Beverages                                                 0.973525   
                      Metal Products                                                   0.944341   
...                                                                                         ...   
Sub-Saharan Africa    Others                                                           0.010742   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...               0.022804   
                      Textiles and Wearing Apparel                                     0.033776   
                      Transport Equipment                                              0.012235   
                      Wood and Paper                                                   0.029068   

                                                                          Europe and Central Asia  \
Group                 Sector                                                                        
East Asia and Pacific Agriculture                                                        0.008850   
                      Electrical and Machinery                                           0.050738   
                      Fishing                                                            0.003310   
                      Food & Beverages                                                   0.012832   
                      Metal Products                                                     0.020276   
...                                                                                           ...   
Sub-Saharan Africa    Others                                                             0.003632   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                 0.023985   
                      Textiles and Wearing Apparel                                       0.076553   
                      Transport Equipment                                                0.016293   
                      Wood and Paper                                                     0.079542   

                                                                          Latin America and Caribbean  \
Group                 Sector                                                                            
East Asia and Pacific Agriculture                                                            0.000760   
                      Electrical and Machinery                                               0.010638   
                      Fishing                                                                0.000227   
                      Food & Beverages                                                       0.001334   
                      Metal Products                                                         0.004299   
...                                                                                               ...   
Sub-Saharan Africa    Others                                                                 0.001164   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                     0.009387   
                      Textiles and Wearing Apparel                                           0.004716   
                      Transport Equipment                                                    0.001268   
                      Wood and Paper                                                         0.002584   

                                                                          Middle East and North Africa  \


In [ ]:
import numpy as np
def kl_divergence(A, B):
    """Calculate the Kullback-Leibler divergence between matrices A and B."""
    # Ensuring the matrices contain no zero elements to avoid division by zero
    A = np.where(A == 0, np.finfo(float).eps, A)
    B = np.where(B == 0, np.finfo(float).eps, B)
    return np.sum(A * np.log(A / B))

R = pd.DataFrame(np.random.randint(5, size=(84, 7)))
R = R.div(R.sum(axis=1),axis=0)
kl_divergence(R.values,benchmark_matrix.values)

211.2486772683912

In [ ]:
import pandas as pd
df = pd.read_csv('IO_cc_primary.csv', index_col=[0,1])
df = df.div(df.sum(axis=1),axis=0)
df[df<0.01]=0
df

East Asia and Pacific  \
Group                 Sector                                                                      
East Asia and Pacific Agriculture                                                      0.982181   
                      Electrical and Machinery                                         0.852470   
                      Fishing                                                          0.981130   
                      Food & Beverages                                                 0.973525   
                      Metal Products                                                   0.944341   
...                                                                                         ...   
Sub-Saharan Africa    Others                                                           0.010742   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...               0.022804   
                      Textiles and Wearing Apparel                                     0.033776   
                      Transport Equipment                                              0.012235   
                      Wood and Paper                                                   0.029068   

                                                                          Europe and Central Asia  \
Group                 Sector                                                                        
East Asia and Pacific Agriculture                                                        0.000000   
                      Electrical and Machinery                                           0.050738   
                      Fishing                                                            0.000000   
                      Food & Beverages                                                   0.012832   
                      Metal Products                                                     0.020276   
...                                                                                           ...   
Sub-Saharan Africa    Others                                                             0.000000   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                 0.023985   
                      Textiles and Wearing Apparel                                       0.076553   
                      Transport Equipment                                                0.016293   
                      Wood and Paper                                                     0.079542   

                                                                          Latin America and Caribbean  \
Group                 Sector                                                                            
East Asia and Pacific Agriculture                                                            0.000000   
                      Electrical and Machinery                                               0.010638   
                      Fishing                                                                0.000000   
                      Food & Beverages                                                       0.000000   
                      Metal Products                                                         0.000000   
...                                                                                               ...   
Sub-Saharan Africa    Others                                                                 0.000000   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                     0.000000   
                      Textiles and Wearing Apparel                                           0.000000   
                      Transport Equipment                                                    0.000000   
                      Wood and Paper                                                         0.000000   

                                                                          Middle East and North Africa  \


In [ ]:
n_countries=7
pop = [1000, 388, 208, 157, 808, 510, 271]

n_products=13
# ray.init()
benchmark_matrix = pd.read_csv('IO_cc_primary.csv', index_col=[0,1])
benchmark_matrix = benchmark_matrix.div(benchmark_matrix.sum(axis=1),axis=0)

parameters={
            "benchmark":benchmark_matrix,
            "n_countries":n_countries,
            "n_products":n_products,
            "countries" : ['{i}'.format(i=i) for i in range(n_countries)],
            "products" : ['{i}'.format(i=i) for i in range(n_products)],
#             "citizens_per_nation" : [100]*n_countries,
            "citizens_per_nation" : pop,
            "A_test":np.random.uniform(0,1,size=(n_countries, n_products)),
            "alpha":np.random.uniform(0,1,size=(n_countries, n_products)),
            "beta":np.random.uniform(0,1,size=(n_countries, n_products)),

            "iterations":2000,
            "Tr_time":1,
            "trade_change":0.05,
            "autarky_time":15000,
            "pricing_algorithm":'cpmu',
                      "utility_algorithm":'geometric',
            "wage_algorithm":'marginal_product',
                      "share" : np.ones(n_countries),
            "shock":None,
            "shock_time":10000,
            "cm_time":1,
            "d":0.000,
            "innovation":False,
            "innovation_time":10000,
            "gamma":1,
            "eta":0.01,
            "weights":None,
            "elasticities":None,
                      "sigma":None
        }
production, income, trades_df, df2 =  gulden_vectorised(case="tune_session", n_countries=parameters["n_countries"], n_products=parameters["n_products"], countries=parameters["countries"], products=parameters["products"], citizens_per_nation=parameters["citizens_per_nation"], A=parameters["A_test"], alpha=parameters["alpha"], beta=parameters["beta"],share=parameters["share"],
                        iterations=parameters["iterations"], Tr_time=parameters["Tr_time"], trade_change=parameters["trade_change"], autarky_time=parameters["autarky_time"], pricing_algorithm=parameters["pricing_algorithm"],
                        utility_algorithm=parameters["utility_algorithm"], wage_algorithm=parameters["wage_algorithm"],

                        csv=False, plot=False, shock=parameters["shock"], shock_time=parameters["shock_time"], cm_time=parameters["cm_time"], d=parameters["d"],
                        innovation=parameters["innovation"], innovation_time=parameters["innovation_time"], gamma=parameters["gamma"], eta=parameters["eta"], weights=parameters["weights"], elasticities=parameters["elasticities"],
                        sigma=parameters["sigma"])

100%|██████████| 2000/2000 [04:39<00:00,  7.15it/s]


In [ ]:
num=df2._get_numeric_data()
num[num<0.01]=0
num

country              0         1         2         3         4         5  \
Group Sector                                                               
0     1       0.864995  0.000000  0.000000  0.000000  0.045959  0.046095   
      2       0.972905  0.000000  0.000000  0.000000  0.000000  0.011521   
      3       0.838895  0.000000  0.016659  0.000000  0.048885  0.049037   
      4       0.812235  0.031735  0.000000  0.018227  0.044114  0.049811   
      5       0.805913  0.012818  0.014613  0.023693  0.049561  0.049687   
...                ...       ...       ...       ...       ...       ...   
6     8       0.000000  0.000000  0.000000  0.000000  0.000000  0.029848   
      9       0.039535  0.000000  0.000000  0.000000  0.039406  0.000000   
      10      0.046481  0.000000  0.000000  0.000000  0.023316  0.047452   
      11      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
      12      0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   

country              6  
Group Sector            
0     1       0.041101  
      2       0.000000  
      3       0.044560  
      4       0.039453  
      5       0.043715  
...                ...  
6     8       0.957289  
      9       0.909242  
      10      0.862579  
      11      0.992263  
      12      0.997889  

[84 rows x 7 columns]

In [ ]:
# benchmark_matrix[benchmark_matrix<0.01]

East Asia and Pacific  \
Group                 Sector                                                                      
East Asia and Pacific Agriculture                                                           NaN   
                      Electrical and Machinery                                              NaN   
                      Fishing                                                               NaN   
                      Food & Beverages                                                      NaN   
                      Metal Products                                                        NaN   
...                                                                                         ...   
Sub-Saharan Africa    Others                                                                NaN   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                    NaN   
                      Textiles and Wearing Apparel                                          NaN   
                      Transport Equipment                                                   NaN   
                      Wood and Paper                                                        NaN   

                                                                          Europe and Central Asia  \
Group                 Sector                                                                        
East Asia and Pacific Agriculture                                                        0.008850   
                      Electrical and Machinery                                                NaN   
                      Fishing                                                            0.003310   
                      Food & Beverages                                                        NaN   
                      Metal Products                                                          NaN   
...                                                                                           ...   
Sub-Saharan Africa    Others                                                             0.003632   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                      NaN   
                      Textiles and Wearing Apparel                                            NaN   
                      Transport Equipment                                                     NaN   
                      Wood and Paper                                                          NaN   

                                                                          Latin America and Caribbean  \
Group                 Sector                                                                            
East Asia and Pacific Agriculture                                                            0.000760   
                      Electrical and Machinery                                                    NaN   
                      Fishing                                                                0.000227   
                      Food & Beverages                                                       0.001334   
                      Metal Products                                                         0.004299   
...                                                                                               ...   
Sub-Saharan Africa    Others                                                                 0.001164   
                      Petroleum, Chemical and Non-Metallic Mineral Pr...                     0.009387   
                      Textiles and Wearing Apparel                                           0.004716   
                      Transport Equipment                                                    0.001268   
                      Wood and Paper                                                         0.002584   

                                                                          Middle East and North Africa  \
